<a href="https://colab.research.google.com/github/nkanungo/S27/blob/main/capstone_pretrain_llms_(1).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

[Source](https://colab.research.google.com/drive/1BiQiw31DT7-cDp1-0ySXvvhzqomTdI-o?usp=sharing&pli=1&authuser=5#scrollTo=_kbS7nRxcMt7)

In [1]:
!pip install -q -U trl transformers accelerate git+https://github.com/huggingface/peft.git
!pip install -q datasets bitsandbytes einops wandb

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 141.1/141.1 kB 3.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.2/8.2 MB 27.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 270.9/270.9 kB 33.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 507.1/507.1 kB 38.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.9/78.9 kB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 15.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 19.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.0/105.0 MB 13.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 6.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 86.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196

In [2]:

#|export
def clean_ipython_hist():
    # Code in this function mainly copied from IPython source
    if not 'get_ipython' in globals(): return
    ip = get_ipython()
    user_ns = ip.user_ns
    ip.displayhook.flush()
    pc = ip.displayhook.prompt_count + 1
    for n in range(1, pc): user_ns.pop('_i'+repr(n),None)
    user_ns.update(dict(_i='',_ii='',_iii=''))
    hm = ip.history_manager
    hm.input_hist_parsed[:] = [''] * pc
    hm.input_hist_raw[:] = [''] * pc
    hm._i = hm._ii = hm._iii = hm._i00 =  ''

In [3]:
#|export
def clean_tb():
    # h/t Piotr Czapla
    if hasattr(sys, 'last_traceback'):
        traceback.clear_frames(sys.last_traceback)
        delattr(sys, 'last_traceback')
    if hasattr(sys, 'last_type'): delattr(sys, 'last_type')
    if hasattr(sys, 'last_value'): delattr(sys, 'last_value')



In [4]:

#|export
def clean_mem():
    clean_tb()
    clean_ipython_hist()
    gc.collect()
    torch.cuda.empty_cache()

In [9]:
import sys, traceback,gc
import torch
#clean_mem()

In [10]:
import datasets
from datasets import load_dataset
dataset_name = "togethercomputer/RedPajama-Data-V2"
train_dataset = load_dataset(dataset_name,'sample', split="train")


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/datasets/load.py:1429: FutureWarning: The repository for togethercomputer/RedPajama-Data-V2 contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/togethercomputer/RedPajama-Data-V2
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this dataset from the next m

Generating train split: 0 examples [00:00, ? examples/s]

In [ ]:
#convert the dataset to pandas dataframe
# df = dataset.to_pandas()
# assistances = df[(df['role'] == 'assistant') & (df['rank'] == 0.0)]
# prompters = df[df['role'] == 'prompter']
# prompters.set_index('message_id',inplace=True)
# assistant_prompt_values = []
# for _,row in assistances.iterrows():
#   prompt_text = prompters.loc[row.parent_id,'text']
#   new_row = "### Human: " + prompt_text + "### Assistant: " + row.text
#   assistant_prompt_values.append(new_row)

# assistances['prompt_assistance_text'] = assistant_prompt_values
# # convert into HG dataset
# finetuning_dataset = datasets.Dataset.from_pandas(assistances)
# finetuning_dataset['prompt_assistance_text'][:3]

In [ ]:
pip install flash_attn

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 10.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.2/307.2 kB 12.4 MB/s eta 0:00:00
  Created wheel for flash_attn: filename=flash_attn-2.4.2-cp310-cp310-linux_x86_64.whl size=113714653 sha256=560df8869000f20f44af8ff42721c3d08ccfe5624bdc3c00e056a783e2a54fb9
  Stored in directory: /root/.cache/pip/wheels/9d/cf/7f/d14555553b5b30698dae0a4159fdd058157e7021cec565ecaa
Successfully built flash_attn


In [11]:
# import torch
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, AutoTokenizer, AutoConfig


# model_name = "microsoft/phi-2"

# bnb_config = AutoConfig.from_pretrained(
#     model_name,
#     load_in_4bit=True,
#     bnb_4bit_quant_type="nf4",
#     bnb_4bit_compute_dtype=torch.float16,
# )

# model = AutoModelForCausalLM.from_config(
#     bnb_config,
#     trust_remote_code=True
# )
# model.config.use_cache = False


import torch
from transformers import AutoModelForCausalLM, AutoConfig

model_name = "microsoft/phi-2"

# Use AutoConfig to load the model configuration
config = AutoConfig.from_pretrained(
    model_name,
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.float16,
)

# Instantiate the model using AutoModelForCausalLM and the configuration
model = AutoModelForCausalLM.from_config(config)

# Disable caching
model.config.use_cache = False

config.json:   0%|          | 0.00/866 [00:00<?, ?B/s]

In [12]:
from transformers import DataCollatorForLanguageModeling
tokenizer = AutoTokenizer.from_pretrained(model_name, trust_remote_code=True)
tokenizer.pad_token = tokenizer.eos_token
data_collator = DataCollatorForLanguageModeling(tokenizer, mlm=False)


tokenizer_config.json:   0%|          | 0.00/7.34k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/798k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.11M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/1.08k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/99.0 [00:00<?, ?B/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [ ]:
print(model)

In [ ]:
from peft import LoraConfig

lora_alpha = 16
lora_dropout = 0.1
lora_r = 64

peft_config = LoraConfig(
    lora_alpha=lora_alpha,

    lora_dropout=lora_dropout,
    r=lora_r,
    bias="none",
    task_type="CAUSAL_LM",
    target_modules=[
        "Wqkv",
        "fc1",
        "fc2"
    ]
)

In [13]:
from transformers import TrainingArguments

output_dir = "./results"
per_device_train_batch_size = 4
per_device_eval_batch_size = 4
gradient_accumulation_steps = 4
optim = "paged_adamw_32bit"
save_steps = 1000
logging_steps = 1000
learning_rate = 2e-4
max_grad_norm = 0.3
max_steps = 1000
warmup_ratio = 0.03
lr_scheduler_type = "constant"
num_train_epochs=1

training_arguments = TrainingArguments(
    output_dir=output_dir,
    per_device_train_batch_size=per_device_train_batch_size,
    per_device_eval_batch_size=per_device_eval_batch_size,
    gradient_accumulation_steps=gradient_accumulation_steps,
    optim=optim,
    save_steps=save_steps,
    logging_steps=logging_steps,
    learning_rate=learning_rate,
    fp16=True,
    max_grad_norm=max_grad_norm,
    max_steps=max_steps,
    warmup_ratio=warmup_ratio,
    group_by_length=True,
    lr_scheduler_type=lr_scheduler_type,
    num_train_epochs=num_train_epochs,
    #gradient_checkpointing=True,
)

In [ ]:
t_dt = train_dataset[0:50000]
len(t_dt)

4

In [14]:
from trl import SFTTrainer

max_seq_length = 256

trainer = SFTTrainer(
    model=model,
    train_dataset=train_dataset,
    #eval_dataset=valid_dataset
    #peft_config=peft_config,
    dataset_text_field="raw_content",
    max_seq_length=max_seq_length,
    tokenizer=tokenizer,
    args=training_arguments,
)

Map:   0%|          | 0/1050391 [00:00<?, ? examples/s]

In [15]:
for name, module in trainer.model.named_modules():
    if "norm" in name:
        module = module.to(torch.float32)

In [16]:
clean_mem()

In [17]:

trainer.train()

<IPython.core.display.Javascript object>

wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


You're using a CodeGenTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=1000, training_loss=6.70426708984375, metrics={'train_runtime': 4256.6249, 'train_samples_per_second': 3.759, 'train_steps_per_second': 0.235, 'total_flos': 5.749422238887936e+16, 'train_loss': 6.70426708984375, 'epoch': 0.02})

In [19]:
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    HfArgumentParser,
    TrainingArguments,
    pipeline,
    logging,
)

In [21]:
# Run text generation pipeline with our next model
prompt = "What is a large language model?"
pipe = pipeline(task="text-generation", model=model, tokenizer=tokenizer, max_length=200)
result = pipe(f"<s>[INST] {prompt} [/INST]").to()
print(result[0]['generated_text'])

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1636: UserWarning: You are calling .generate() with the `input_ids` being on a device type different than your model's device. `input_ids` is on cpu, whereas the model is on cuda. You may experience unexpected behaviors or slower generation. Please make sure that you have put `input_ids` to the correct device by calling for example input_ids = input_ids.to('cuda') before running `.generate()`.
  warnings.warn(


RuntimeError: Expected all tensors to be on the same device, but found at least two devices, cuda:0 and cpu! (when checking argument for argument index in method wrapper_CUDA__index_select)

In [ ]:
# Run text generation pipeline with our next model
prompt = "What is a model explainability?"
pipe = pipeline(task="text-generation", model=model, tokenizer=tokenizer, max_length=200)
result = pipe(f"<s>[INST] {prompt} [/INST]")
print(result[0]['generated_text'])

<s>[INST] What is a model explainability? [/INST]<s>What is a model explainability?</s>

<s>Model explainability is the ability to understand how a model makes decisions and predictions. It is important because it helps us understand how the model works and how to improve it. It also helps us understand why the model made a certain decision or prediction, which can be useful in many applications.</s>

<s>What are some examples of model explainability?</s>

<s>Some examples of model explainability include:

- Understanding how a neural network makes predictions
- Understanding how a decision tree makes decisions
- Understanding how a linear regression model makes predictions
- Understanding how a random forest makes predictions
- Understanding how a support vector machine makes predictions
- Understanding how a deep learning model makes predictions
- Understanding how a reinforcement learning model makes decisions
- Understanding how a reinforcement learning model makes decisions


In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [ ]:
ls


gdrive/  results/  sample_data/  wandb/


In [ ]:
cd results


/content/results


In [ ]:
ls

checkpoint-10/    checkpoint-280/  checkpoint-470/  checkpoint-660/  checkpoint-850/
checkpoint-100/   checkpoint-290/  checkpoint-480/  checkpoint-670/  checkpoint-860/
checkpoint-1000/  checkpoint-30/   checkpoint-490/  checkpoint-680/  checkpoint-870/
checkpoint-110/   checkpoint-300/  checkpoint-50/   checkpoint-690/  checkpoint-880/
checkpoint-120/   checkpoint-310/  checkpoint-500/  checkpoint-70/   checkpoint-890/
checkpoint-130/   checkpoint-320/  checkpoint-510/  checkpoint-700/  checkpoint-90/
checkpoint-140/   checkpoint-330/  checkpoint-520/  checkpoint-710/  checkpoint-900/
checkpoint-150/   checkpoint-340/  checkpoint-530/  checkpoint-720/  checkpoint-910/
checkpoint-160/   checkpoint-350/  checkpoint-540/  checkpoint-730/  checkpoint-920/
checkpoint-170/   checkpoint-360/  checkpoint-550/  checkpoint-740/  checkpoint-930/
checkpoint-180/   checkpoint-370/  checkpoint-560/  checkpoint-750/  checkpoint-940/
checkpoint-190/   checkpoint-380/  checkpoint-570/  checkpoint-760

In [ ]:
cp -r checkpoint-960/ ../gdrive/MyDrive/

In [ ]:
ls

checkpoint-10/    checkpoint-280/  checkpoint-470/  checkpoint-660/  checkpoint-850/
checkpoint-100/   checkpoint-290/  checkpoint-480/  checkpoint-670/  checkpoint-860/
checkpoint-1000/  checkpoint-30/   checkpoint-490/  checkpoint-680/  checkpoint-870/
checkpoint-110/   checkpoint-300/  checkpoint-50/   checkpoint-690/  checkpoint-880/
checkpoint-120/   checkpoint-310/  checkpoint-500/  checkpoint-70/   checkpoint-890/
checkpoint-130/   checkpoint-320/  checkpoint-510/  checkpoint-700/  checkpoint-90/
checkpoint-140/   checkpoint-330/  checkpoint-520/  checkpoint-710/  checkpoint-900/
checkpoint-150/   checkpoint-340/  checkpoint-530/  checkpoint-720/  checkpoint-910/
checkpoint-160/   checkpoint-350/  checkpoint-540/  checkpoint-730/  checkpoint-920/
checkpoint-170/   checkpoint-360/  checkpoint-550/  checkpoint-740/  checkpoint-930/
checkpoint-180/   checkpoint-370/  checkpoint-560/  checkpoint-750/  checkpoint-940/
checkpoint-190/   checkpoint-380/  checkpoint-570/  checkpoint-760

In [ ]:
ls ../gdrive/MyDrive/

'Colab Notebooks'/
